In [1]:
import requests
from bs4 import BeautifulSoup
import numpy as np
import pandas as pd
import pickle as pkl
from tqdm import tqdm
import nltk, re
from nltk.corpus import stopwords
from nltk import word_tokenize

In [2]:
NnL = pd.read_excel('CharacterData.xlsx',index_col=0)
NnL['WikiText'] = np.nan
NnL['Tokens'] = np.nan

In [3]:
def tokenize(text):
    # Remove URLs
    text = re.sub('http[s]?://\S+', '', text)

    # Exclude punctuation and numbers and set everything to lower case.
    text = word_tokenize(text)
    text = [w.lower() for w in text if w.isalpha()]

    # Exclude stopwords
    text = [w for w in text if not w.lower() in set(stopwords.words('english'))]

    # Save
    return text

In [8]:
texts = np.zeros(len(NnL), dtype=object)
tokens = np.zeros(len(NnL), dtype=object)

for char_idx in tqdm(range(len(NnL))):
    query = requests.get(f"https://harrypotter.fandom.com/api.php?action=parse&page={NnL['Link'].iloc[char_idx].split('/')[-1].split('#')[0]}&format=json").json()
    HTML = query['parse']['text']['*']
    soup = BeautifulSoup(HTML, 'html.parser')

    temp = [i.get_text() for i in soup.find_all('p', class_ = None)]

    if 'At least some content in this article' in temp[0]:
        temp = temp[1:]
    if 'At least some content in this article' in temp[0]:
        temp = temp[1:]
    if 'The title of this article is conjectural.' in temp[0]:
        temp = temp[1:]
    if 'This entry needs to be cleaned up to conform to a higher standard of quality.' in temp[0]:
        temp = temp[1:]
    if 'The topic of this article is of a real-life subject' in temp[0]:
        temp = temp[1:]
    if 'The title of this article intentionally uses incorrect spelling or grammar,' in temp[0]:
        temp = temp[1:]
    if 'This page "shows not" an image, but just a written article.' in temp[0]:
        temp = temp[1:]
    if 'Point me!' in temp[0]:
        temp = temp[1:]
    if 'Point me!' in temp[0]:
        temp = temp[1:]
    if 'At least some content in this article' in temp[0]:
        temp = temp[1:]
    if 'The title of this article is conjectural.' in temp[0]:
        temp = temp[1:]
    if 'Biographical information' in temp[0]:
        temp = temp[1:]
        
    texts[char_idx] = ' '.join(temp)
    tokens[char_idx] = tokenize(texts[char_idx])

NnL['WikiText'] = texts
NnL['Tokens'] = tokens

100%|██████████| 707/707 [08:34<00:00,  1.37it/s] 


In [9]:
NnL

Name                               Link  \
0               Vernon Dursley               /wiki/Vernon_Dursley   
1              Petunia Dursley              /wiki/Petunia_Dursley   
2               Dudley Dursley               /wiki/Dudley_Dursley   
3                  Lily Potter               /wiki/Lily_J._Potter   
4                 James Potter               /wiki/James_Potter_I   
..                         ...                                ...   
702               Hugo Weasley         /wiki/Hugo_Granger-Weasley   
703            Scorpius Malfoy              /wiki/Scorpius_Malfoy   
704           Victoire Weasley             /wiki/Victoire_Weasley   
705         Astoria Greengrass               /wiki/Astoria_Malfoy   
706  James Potter II's friends  /wiki/James_Potter_II%27s_friends   

                                              WikiText  \
0    Vernon Dursley was an English Muggle, husband ...   
1    Petunia Dursley (née Evans) (pre 1960 – pre 20...   
2    Dudley Dursley (b. 23 June 1980)[1] was the Mu...   
3    Lily J.[8] Potter (née Evans) (30 January[1] 1...   
4    England,[2] Great Britain Godric's Hollow, Wes...   
..                                                 ...   
702  Hugo Granger-Weasley was born around 2008 to a...   
703  Scorpius Hyperion Malfoy (b. c. 2006) was a Br...   
704  Victoire Weasley (b. 2 May[1] 2000 or 2001)[2]...   
705  Great Britain Astoria Malfoy[8] (née Greengras...   
706  This group of Hogwarts students were friends o...   

                                                Tokens  
0    [vernon, dursley, english, muggle, husband, pe...  
1    [petunia, dursley, née, evans, pre, pre, engli...  
2    [dudley, dursley, b, june, muggle, son, vernon...  
3    [lily, j, potter, née, evans, january, october...  
4    [england, great, britain, godric, hollow, west...  
..                                                 ...  
702  [hugo, born, around, father, mother, making, t...  
703  [scorpius, hyperion, malfoy, british, wizard, ...  
704  [victoire, weasley, b, may, witch, eldest, chi...  
705  [great, britain, astoria, malfoy, née, greengr...  
706  [group, hogwarts, students, friends, james, po...  

[707 rows x 4 columns]

In [10]:
NnL.to_csv('CharacterWikis.csv',index=False)

In [11]:
[NnL.WikiText.iloc[i] for i in range(len(NnL))]

['Vernon Dursley was an English Muggle, husband of Petunia Evans, father of Dudley Dursley and uncle by marriage of Harry Potter. He lived at 4 Privet Drive, Little Whinging, Surrey, along with his wife and son for twenty years until they were forced into hiding during the escalation of the Second Wizarding War. \n After Petunia\'s sister Lily and brother-in-law, James Potter, were killed by Voldemort in their own home, Petunia remained the sole surviving blood relative of Harry\'s. Both Wizard and Muggle law demanded that Petunia and Vernon be the new legal guardians of Harry Potter, which they accepted (albeit reluctantly). However, they disliked Harry and treated him badly, while spoiling and pampering Dudley.\n When Harry was sent a letter from Hogwarts School of Witchcraft and Wizardry, Vernon got very angry, as he detested anything to do with magic. He was a former student of Smeltings Academy and a director of the Grunnings drill manufacturing company. In 1997, Vernon, Petunia a